# Introduction

Looking for a apartment in the city you want to study can be a very difficult step, because you have to consider some factors like cost, location, if there are restaurants and supermarkets nearby, etc. So, using clusters to find a great place to live can be very helpful. Even more if the best and worst place can be shown in a map. This clustering method can help a lot of future students seeking for a great apartment.

# Data

The data used in this research report is provided by the New York University Spatial Data Repository, https://geo.nyu.edu/catalog/nyu_2451_34572. And, from Foursquare I extracted the information about the supermarkets, nightclubs, restaurants, coffee shops, cinemas, universities and other locations important for students that are nearby the neighborhoods and did cluster analysis to determine the best and the worst places to search for an apartment. 

## Import Libraries

In [18]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

#!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

#!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')

Libraries imported.


In [4]:
with open('newyork_data.json') as json_data:
    newyork_data = json.load(json_data)

In [5]:
neighborhoods_data = newyork_data['features']

## Transform data into a pandas dataframe


In [6]:
# define the dataframe columns
column_names = ['Borough', 'Neighborhood', 'Latitude', 'Longitude'] 

# instantiate the dataframe
neighborhoods = pd.DataFrame(columns=column_names)

In [7]:
for data in neighborhoods_data:
    borough = neighborhood_name = data['properties']['borough'] 
    neighborhood_name = data['properties']['name']
        
    neighborhood_latlon = data['geometry']['coordinates']
    neighborhood_lat = neighborhood_latlon[1]
    neighborhood_lon = neighborhood_latlon[0]
    
    neighborhoods = neighborhoods.append({'Borough': borough,
                                          'Neighborhood': neighborhood_name,
                                          'Latitude': neighborhood_lat,
                                          'Longitude': neighborhood_lon}, ignore_index=True)

## Define Foursquare Credentials and Version

In [25]:
CLIENT_ID = 'YUXYDJBSVSDRSVPJAIYIL0RKMBEM1RMT2HLCN4ATLT51GT2K' # your Foursquare ID
CLIENT_SECRET = 'Z10WLH2YRBC523SPKKD2UTH3FZXDLW5I1KAQ5LH5XEMBYSQV' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: YUXYDJBSVSDRSVPJAIYIL0RKMBEM1RMT2HLCN4ATLT51GT2K
CLIENT_SECRET:Z10WLH2YRBC523SPKKD2UTH3FZXDLW5I1KAQ5LH5XEMBYSQV


## Use geopy library to get the latitude and longitude values of New York City.

In [26]:
address = 'New York City, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of New York City are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of New York City are 40.7127281, -74.0060152.


In [27]:
# create map of New York using latitude and longitude values
map_newyork = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(neighborhoods['Latitude'], neighborhoods['Longitude'], neighborhoods['Borough'], neighborhoods['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_newyork)  
    
map_newyork

## Getting the top 100 venues that are in New York within a radius of 200 meters

In [28]:
LIMIT = 100
radius = 200
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [29]:
manhattan_data = neighborhoods[neighborhoods['Borough'] == 'Manhattan'].reset_index(drop=True)
brooklyn_data = neighborhoods[neighborhoods['Borough'] == 'Brooklyn'].reset_index(drop=True)
bronx_data = neighborhoods[neighborhoods['Borough'] == 'Bronx'].reset_index(drop=True)
queens_data = neighborhoods[neighborhoods['Borough'] == 'Queens'].reset_index(drop=True)
staten_data = neighborhoods[neighborhoods['Borough'] == 'Staten Island'].reset_index(drop=True)

frames = [manhattan_data, brooklyn_data, bronx_data, queens_data, staten_data]
df = pd.concat(frames)
df_ny = df.reset_index(drop = True)

In [30]:
venues = getNearbyVenues(names = df_ny['Neighborhood'],
                        latitudes = df_ny['Latitude'],
                        longitudes = df_ny['Longitude'])

Marble Hill
Chinatown
Washington Heights
Inwood
Hamilton Heights
Manhattanville
Central Harlem
East Harlem
Upper East Side
Yorkville
Lenox Hill
Roosevelt Island
Upper West Side
Lincoln Square
Clinton
Midtown
Murray Hill
Chelsea
Greenwich Village
East Village
Lower East Side
Tribeca
Little Italy
Soho
West Village
Manhattan Valley
Morningside Heights
Gramercy
Battery Park City
Financial District
Carnegie Hill
Noho
Civic Center
Midtown South
Sutton Place
Turtle Bay
Tudor City
Stuyvesant Town
Flatiron
Hudson Yards
Bay Ridge
Bensonhurst
Sunset Park
Greenpoint
Gravesend
Brighton Beach
Sheepshead Bay
Manhattan Terrace
Flatbush
Crown Heights
East Flatbush
Kensington
Windsor Terrace
Prospect Heights
Brownsville
Williamsburg
Bushwick
Bedford Stuyvesant
Brooklyn Heights
Cobble Hill
Carroll Gardens
Red Hook
Gowanus
Fort Greene
Park Slope
Cypress Hills
East New York
Starrett City
Canarsie
Flatlands
Mill Island
Manhattan Beach
Coney Island
Bath Beach
Borough Park
Dyker Heights
Gerritsen Beach
Marine

## Analyze Each Neighborhood

In [31]:
# one hot encoding
ny_onehot = pd.get_dummies(venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
ny_onehot['Neighborhood'] = venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [ny_onehot.columns[-1]] + list(ny_onehot.columns[:-1])
ny_onehot = ny_onehot[fixed_columns]

ny_onehot.head()

Yoga Studio  Accessories Store  Adult Boutique  Afghan Restaurant  \
0            0                  0               0                  0   
1            1                  0               0                  0   
2            0                  0               0                  0   
3            0                  0               0                  0   
4            0                  0               0                  0   

   African Restaurant  American Restaurant  Antique Shop  Arcade  \
0                   0                    0             0       0   
1                   0                    0             0       0   
2                   0                    0             0       0   
3                   0                    0             0       0   
4                   0                    0             0       0   

   Arepa Restaurant  Argentinian Restaurant  Art Gallery  Art Museum  \
0                 0                       0            0           0   
1                 0                       0            0           0   
2                 0                       0            0           0   
3                 0                       0            0           0   
4                 0                       0            0           0   

   Arts & Crafts Store  Arts & Entertainment  Asian Restaurant  \
0                    0                     0                 0   
1                    0                     0                 0   
2                    0                     0                 0   
3                    0                     0                 0   
4                    0                     0                 0   

   Athletics & Sports  Auditorium  Australian Restaurant  Austrian Restaurant  \
0                   0           0                      0                    0   
1                   0           0                      0                    0   
2                   0           0                      0                    0   
3                   0           0                      0                    0   
4                   0           0                      0                    0   

   Auto Dealership  Auto Garage  Automotive Shop  BBQ Joint  Baby Store  \
0                0            0                0          0           0   
1                0            0                0          0           0   
2                0            0                0          0           0   
3                0            0                0          0           0   
4                0            0                0          0           0   

   Bagel Shop  Bakery  Bank  Bar  Baseball Field  Baseball Stadium  \
0           0       0     0    0               0                 0   
1           0       0     0    0               0                 0   
2           0       0     0    0               0                 0   
3           0       0     0    0               0                 0   
4           0       0     0    0               0                 0   

   Basketball Court  Bath House  Beach  Beach Bar  Bed & Breakfast  Beer Bar  \
0                 0           0      0          0                0         0   
1                 0           0      0          0                0         0   
2                 0           0      0          0                0         0   
3                 0           0      0          0                0         0   
4                 0           0      0          0                0         0   

   Beer Garden  Beer Store  Big Box Store  Bike Rental / Bike Share  \
0            0           0              0                         0   
1            0           0              0                         0   
2            0           0              0                         0   
3            0           0              0                         0   
4            0           0              0                         0   

   Bike Shop  Bike Trail  Bistro  Board Shop  Boat or Ferry  Boo

In [32]:
ny_onehot_p = ny_onehot.groupby(['Neighborhood']).count()
ny_onehot_p['my_sum'] = ny_onehot_p.iloc[:, 1:].sum(1)
ny_onehot_p['my_sum'].plot(kind='area')

## Next, let's group rows by neighborhood and by taking the mean of the frequency of occurrence of each category

In [33]:
ny_grouped = ny_onehot.groupby('Neighborhood').mean().reset_index()
ny_grouped

Neighborhood  Yoga Studio  Accessories Store  \
0                     Allerton     0.000000           0.000000   
1                     Annadale     0.000000           0.000000   
2                Arden Heights     0.000000           0.000000   
3                    Arlington     0.000000           0.000000   
4                     Arrochar     0.000000           0.000000   
5                      Arverne     0.000000           0.000000   
6                      Astoria     0.000000           0.000000   
7              Astoria Heights     0.000000           0.000000   
8                   Auburndale     0.000000           0.000000   
9                   Bath Beach     0.000000           0.000000   
10           Battery Park City     0.000000           0.000000   
11                   Bay Ridge     0.011628           0.000000   
12                 Bay Terrace     0.000000           0.021277   
13                  Baychester     0.000000           0.000000   
14                     Bayside     0.013514           0.000000   
15                   Bayswater     0.000000           0.000000   
16                Bedford Park     0.000000           0.000000   
17          Bedford Stuyvesant     0.000000           0.000000   
18                  Beechhurst     0.066667           0.000000   
19                    Bellaire     0.000000           0.000000   
20                Belle Harbor     0.000000           0.000000   
21                   Bellerose     0.000000           0.000000   
22                     Belmont     0.000000           0.000000   
23                 Bensonhurst     0.000000           0.000000   
24                Bergen Beach     0.000000           0.000000   
25                  Blissville     0.000000           0.000000   
26                  Bloomfield     0.000000           0.000000   
27                 Boerum Hill     0.023256           0.000000   
28                Borough Park     0.000000           0.000000   
29                Breezy Point     0.000000           0.000000   
30                   Briarwood     0.000000           0.000000   
31              Brighton Beach     0.000000           0.000000   
32               Broad Channel     0.000000           0.000000   
33           Broadway Junction     0.000000           0.000000   
34                   Bronxdale     0.000000           0.000000   
35            Brooklyn Heights     0.050000           0.000000   
36                  Brookville     0.000000           0.000000   
37                 Brownsville     0.000000           0.000000   
38                  Bulls Head     0.000000           0.000000   
39                    Bushwick     0.000000           0.000000   
40                Butler Manor     0.000000           0.000000   
41             Cambria Heights     0.000000           0.000000   
42                    Canarsie     0.000000           0.000000   
43               Carnegie Hill     0.030000           0.000000   
44             Carroll Gardens     0.000000           0.000000   
45                 Castle Hill     0.000000           0.000000   
46           Castleton Corners     0.000000           0.000000   
47              Central Harlem     0.000000           0.000000   
48                  Charleston     0.000000           0.000000   
49                     Chelsea     0.000000           0.000000   
50                   Chinatown     0.010000           0.000000   
51                 City Island     0.000000           0.000000   
52                   City Line     0.000000           0.000000   
53                Civic Center     0.030000           0.000000   
54           Claremont Village     0.000000           0.000000   
55                Clason Point     0.000000           0.000000   
56                     Clifton     0.000000           0.000000   
57                     Clinton     0.000000           0.000000   
58                Clinton Hill     0.032258           0.000000   
59                  Co-op City     0.000000           0.05

In [34]:
ny_grouped.shape

(301, 433)

## Print each neighborhood along with the top 10 most common venues

In [35]:
num_top_venues = 10

for hood in ny_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = ny_grouped[ny_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Allerton----
                   venue  freq
0            Pizza Place  0.15
1     Chinese Restaurant  0.09
2          Deli / Bodega  0.06
3            Supermarket  0.06
4         Cosmetics Shop  0.06
5           Dessert Shop  0.03
6     Spanish Restaurant  0.03
7   Fast Food Restaurant  0.03
8  Check Cashing Service  0.03
9             Playground  0.03


----Annadale----
                 venue  freq
0          Pizza Place  0.18
1             Pharmacy  0.09
2     Sushi Restaurant  0.09
3        Train Station  0.09
4           Sports Bar  0.09
5                Diner  0.09
6  American Restaurant  0.09
7           Restaurant  0.09
8         Dance Studio  0.09
9        Deli / Bodega  0.09


----Arden Heights----
                           venue  freq
0                       Pharmacy  0.17
1                  Deli / Bodega  0.17
2                       Bus Stop  0.17
3                   Home Service  0.17
4                    Coffee Shop  0.17
5                    Pizza Place  0.17
6  Pape

## Let's put that into a pandas dataframe

In [36]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [37]:
num_top_venues = 5

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = ny_grouped['Neighborhood']

for ind in np.arange(ny_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(ny_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0       Allerton           Pizza Place    Chinese Restaurant   
1       Annadale           Pizza Place                 Diner   
2  Arden Heights              Pharmacy         Deli / Bodega   
3      Arlington              Bus Stop          Intersection   
4       Arrochar              Bus Stop            Bagel Shop   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  
0           Supermarket         Deli / Bodega        Cosmetics Shop  
1         Train Station            Sports Bar          Dance Studio  
2              Bus Stop           Coffee Shop          Home Service  
3   American Restaurant         Deli / Bodega         Women's Store  
4    Italian Restaurant         Deli / Bodega           Pizza Place

In [38]:
# set number of clusters
kclusters = 3

ny_grouped_clustering = ny_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(ny_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:15] 

array([1, 1, 0, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1], dtype=int32)

In [39]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

ny_merged = df_ny

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
ny_merged = ny_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

ny_merged.head() # check the last columns!

Borough        Neighborhood   Latitude  Longitude  Cluster Labels  \
0  Manhattan         Marble Hill  40.876551 -73.910660             1.0   
1  Manhattan           Chinatown  40.715618 -73.994279             1.0   
2  Manhattan  Washington Heights  40.851903 -73.936900             1.0   
3  Manhattan              Inwood  40.867684 -73.921210             1.0   
4  Manhattan    Hamilton Heights  40.823604 -73.949688             1.0   

  1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0           Coffee Shop        Sandwich Place           Yoga Studio   
1    Chinese Restaurant          Cocktail Bar   American Restaurant   
2                  Café                Bakery         Grocery Store   
3                  Café    Mexican Restaurant            Restaurant   
4           Pizza Place                  Café           Coffee Shop   

  4th Most Common Venue 5th Most Common Venue  
0            Kids Store         Shopping Mall  
1                   Spa                Bakery  
2     Mobile Phone Shop    Spanish Restaurant  
3                Lounge                Bakery  
4    Mexican Restaurant           Yoga Studio

In [40]:
ny_merged.dropna(axis=0, inplace = True)
ny_merged['Cluster Labels'] = ny_merged['Cluster Labels'].apply(np.int64)
ny_merged.tail()

Borough     Neighborhood   Latitude  Longitude  Cluster Labels  \
301  Staten Island      Egbertville  40.579119 -74.127272               1   
302  Staten Island     Prince's Bay  40.526264 -74.201526               1   
303  Staten Island  Lighthouse Hill  40.576506 -74.137927               1   
304  Staten Island  Richmond Valley  40.519541 -74.229571               1   
305  Staten Island        Fox Hills  40.617311 -74.081740               0   

    1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
301    Italian Restaurant        Cosmetics Shop            Smoke Shop   
302           Pizza Place            Food Truck                  Bank   
303                  Café    Italian Restaurant                 Trail   
304                  Bank       Bubble Tea Shop        Sandwich Place   
305        Sandwich Place    African Restaurant         Deli / Bodega   

    4th Most Common Venue 5th Most Common Venue  
301            Bagel Shop        Clothing Store  
302             Pet Store            Bagel Shop  
303                   Spa            Art Museum  
304         Deli / Bodega         Smoothie Shop  
305              Bus Stop            Playground

In [41]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=10)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(ny_merged['Latitude'], ny_merged['Longitude'], ny_merged['Neighborhood'], ny_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

In [42]:
ny_merged.loc[ny_merged['Cluster Labels'] == 0, ny_merged.columns[[1] + list(range(5, ny_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
71    Manhattan Beach              Bus Stop            Playground   
83         Ocean Hill         Deli / Bodega              Bus Stop   
205      Breezy Point                 Trail                 Beach   
212          Neponsit                 Beach         Women's Store   
226        Brookville         Deli / Bodega         Women's Store   
237           Roxbury             Irish Pub                 Beach   
240           Hammels                 Beach   Fried Chicken Joint   
244      New Brighton              Bus Stop         Deli / Bodega   
248       Grymes Hill              Bus Stop               Dog Run   
250       South Beach                 Beach                  Pier   
251     Port Richmond              Bus Stop   Rental Car Location   
252  Mariner's Harbor    Italian Restaurant         Deli / Bodega   
263       Tottenville           Frame Store         Deli / Bodega   
267         Park Hill              Bus Stop           Coffee Shop   
269      Graniteville              Bus Stop           Supermarket   
270         Arlington              Bus Stop          Intersection   
275     Midland Beach                 Beach            Restaurant   
281      Butler Manor                  Pool        Baseball Field   
284     Arden Heights              Pharmacy         Deli / Bodega   
288        Bloomfield     Recreation Center                  Park   
291       Shore Acres    Italian Restaurant         Deli / Bodega   
295     Randall Manor              Bus Stop            Playground   
299       Willowbrook              Bus Stop           Pizza Place   
305         Fox Hills        Sandwich Place    African Restaurant   

          3rd Most Common Venue 4th Most Common Venue  \
71               Sandwich Place       Harbor / Marina   
83                   Playground         Grocery Store   
205         Monument / Landmark         Women's Store   
212  Financial or Legal Service         Event Service   
226           Fish & Chips Shop         Event Service   
237                       Trail         Deli / Bodega   
240                     Dog Run            Food Truck   
244                        Park            Playground   
248               Women's Store     Fish & Chips Shop   
250          Athletics & Sports         Deli / Bodega   
251                  Playground                  Food   
252           Fish & Chips Shop         Event Service   
263          Mexican Restaurant          Home Service   
267        Gym / Fitness Center                 Hotel   
269               Boat or Ferry        Sandwich Place   
270         American Restaurant         Deli / Bodega   
275              Baseball Field                  Café   
281           Convenience Store              Bus Stop   
284                    Bus Stop           Coffee Shop   
288                  Theme Park              Bus Stop   
291                    Bus Stop          Intersection   
295                  Bagel Shop                  Park   
299                Intersection                   Spa   
305               Deli / Bodega              Bus Stop   

          5th Most Common Venue  
71                         Café  
83          Fried Chicken Joint  
205  Financial or Legal Service  
212                 Event Space  
226                 Event Space  
237        Fast Food Restaurant  
240                 Bus Station  
244               Bowling Alley  
248                 Event Space  
250                    Bus Stop  
251                  Donut Shop  
252                 Event Space  
263                    Bus Stop  
267          Athletics & Sports  
269               Women's Store  
270               Women's Store  
275          Chinese Restaurant  
281               Women's Store  
284                Home Service  
288              Discount Store  
291                         Bar  
295               Women's Store  
299                  Bagel Shop  
305                  Playground

In [43]:
ny_merged.loc[ny_merged['Cluster Labels'] == 1, ny_merged.columns[[1] + list(range(5, ny_merged.shape[1]))]]

Neighborhood          1st Most Common Venue  \
0                  Marble Hill                    Coffee Shop   
1                    Chinatown             Chinese Restaurant   
2           Washington Heights                           Café   
3                       Inwood                           Café   
4             Hamilton Heights                    Pizza Place   
5               Manhattanville                    Coffee Shop   
6               Central Harlem             African Restaurant   
7                  East Harlem             Mexican Restaurant   
8              Upper East Side             Italian Restaurant   
9                    Yorkville             Italian Restaurant   
10                  Lenox Hill                    Coffee Shop   
11            Roosevelt Island                 Sandwich Place   
12             Upper West Side             Italian Restaurant   
13              Lincoln Square                        Theater   
14                     Clinton                        Theater   
15                     Midtown                          Hotel   
16                 Murray Hill              Korean Restaurant   
17                     Chelsea                    Coffee Shop   
18           Greenwich Village             Italian Restaurant   
19                East Village                            Bar   
20             Lower East Side                    Art Gallery   
21                     Tribeca            American Restaurant   
22                Little Italy                           Café   
23                        Soho                 Clothing Store   
24                West Village             Italian Restaurant   
25            Manhattan Valley                            Bar   
26         Morningside Heights                           Park   
27                    Gramercy                            Bar   
28           Battery Park City                           Park   
29          Financial District                    Coffee Shop   
30               Carnegie Hill                    Coffee Shop   
31                        Noho             Italian Restaurant   
32                Civic Center           Gym / Fitness Center   
33               Midtown South              Korean Restaurant   
34                Sutton Place           Gym / Fitness Center   
35                  Turtle Bay             Italian Restaurant   
36                  Tudor City                           Café   
37             Stuyvesant Town                            Bar   
38                    Flatiron            Japanese Restaurant   
39                Hudson Yards            American Restaurant   
40                   Bay Ridge             Italian Restaurant   
41                 Bensonhurst               Sushi Restaurant   
42                 Sunset Park                           Bank   
43                  Greenpoint                            Bar   
44                   Gravesend             Chinese Restaurant   
45              Brighton Beach             Russian Restaurant   
46              Sheepshead Bay             Turkish Restaurant   
47           Manhattan Terrace                     Donut Shop   
48                    Flatbush           Caribbean Restaurant   
49               Crown Heights                    Pizza Place   
50               East Flatbush           Fast Food Restaurant   
51                  Kensington                  Grocery Store   
52             Windsor Terrace                  Deli / Bodega   
53            Prospect Heights                            Bar   
54                 Brownsville                     Restaurant   
55                Williamsburg                            Bar   
56                    Bushwick                            Bar   
57          Bedford Stuyvesant                    Pizza Place   
58            Brooklyn Heights                    Yoga Studio   
59                 Cobble Hill                            Bar   
60             Carroll Gardens             Italian Re

In [44]:
ny_merged.loc[ny_merged['Cluster Labels'] == 2, ny_merged.columns[[1] + list(range(5, ny_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
136  Clason Point                  Park              Bus Stop   
225    Somerville                  Park         Women's Store   
249     Todt Hill                 Trail                  Park   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  
136         Grocery Store                  Pool         Boat or Ferry  
225   Filipino Restaurant  Ethiopian Restaurant         Event Service  
249         Women's Store   Empanada Restaurant  Ethiopian Restaurant